In [57]:
import pandas as pd
import cufflinks as cf
from tqdm import tqdm
import folium
import logging
from folium.plugins import MarkerCluster, FastMarkerCluster
from folium import FeatureGroup, LayerControl, Map, Marker


In [24]:
cf.go_offline()

In [2]:
df = pd.read_csv('film_locations_geocoded.csv.gz')

In [3]:
df.head()

Unnamed: 0  EventID        EventType        StartDateTime  \
0        4150   325488  Shooting Permit  2017-01-02 00:00:00   
1        4151   324505  Shooting Permit  2017-01-03 07:00:00   
2        4151   324505  Shooting Permit  2017-01-03 07:00:00   
3        4151   324505  Shooting Permit  2017-01-03 07:00:00   
4        4151   324505  Shooting Permit  2017-01-03 07:00:00   

           EndDateTime            EnteredOn  \
0  2017-01-02 09:00:00  2016-12-30 05:47:38   
1  2017-01-03 23:00:00  2016-12-16 16:55:04   
2  2017-01-03 23:00:00  2016-12-16 16:55:04   
3  2017-01-03 23:00:00  2016-12-16 16:55:04   
4  2017-01-03 23:00:00  2016-12-16 16:55:04   

                                      EventAgency  \
0  Mayor's Office of Film, Theatre & Broadcasting   
1  Mayor's Office of Film, Theatre & Broadcasting   
2  Mayor's Office of Film, Theatre & Broadcasting   
3  Mayor's Office of Film, Theatre & Broadcasting   
4  Mayor's Office of Film, Theatre & Broadcasting   

                                         ParkingHeld    Borough  \
0     WEST   44 STREET between BROADWAY and 6 AVENUE  Manhattan   
1  LOCUST AVENUE between EAST  139 STREET and EAS...      Bronx   
2  LOCUST AVENUE between EAST  139 STREET and EAS...      Bronx   
3  LOCUST AVENUE between EAST  139 STREET and EAS...      Bronx   
4  LOCUST AVENUE between EAST  139 STREET and EAS...      Bronx   

  CommunityBoard(s)    ...      SubCategoryName                   Country  \
0                 5    ...         Morning Show  United States of America   
1                 1    ...      Episodic series  United States of America   
2                 1    ...      Episodic series  United States of America   
3                 1    ...      Episodic series  United States of America   
4                 1    ...      Episodic series  United States of America   

  ZipCode(s) duration_hours event_days_before  \
0      10036            9.0                 2   
1      10454           16.0                17   
2      10454           16.0                17   
3      10454           16.0                17   
4      10454           16.0                17   

                                           locations  num_locations  \
0  ['WEST   44 STREET between BROADWAY and 6 AVEN...              1   
1  ['LOCUST AVENUE between EAST  139 STREET and E...              4   
2  ['LOCUST AVENUE between EAST  139 STREET and E...              4   
3  ['LOCUST AVENUE between EAST  139 STREET and E...              4   
4  ['LOCUST AVENUE between EAST  139 STREET and E...              4   

                                            location   latitude  longitude  
0  WEST   44 STREET between BROADWAY and 6 AVENUE...  40.757156 -73.984803  
1  LOCUST AVENUE between EAST  139 STREET and EAS...  40.810089 -73.922740  
2  EAST  140 STREET between LOCUST AVENUE and WAL...  40.808927 -73.918436  
3  WALNUT AVENUE between EAST  139 STREET and EAS...  40.810089 -73.922740  
4  EAST  139 STREET between WALNUT AVENUE and LOC...  40.807513 -73.917024  

[5 rows x 22 columns]

In [4]:
df.columns

Index(['Unnamed: 0', 'EventID', 'EventType', 'StartDateTime', 'EndDateTime',
       'EnteredOn', 'EventAgency', 'ParkingHeld', 'Borough',
       'CommunityBoard(s)', 'PolicePrecinct(s)', 'Category', 'SubCategoryName',
       'Country', 'ZipCode(s)', 'duration_hours', 'event_days_before',
       'locations', 'num_locations', 'location', 'latitude', 'longitude'],
      dtype='object')

In [7]:
df['Country'].value_counts()

United States of America    29964
United Kingdom                 16
Ireland                        14
Australia                       1
Name: Country, dtype: int64

In [17]:
df = df[['EventID','EventType','StartDateTime', 'EndDateTime',
       'EnteredOn','Category','SubCategoryName','duration_hours' ,'location', 'latitude', 'longitude']]
df.head()

EventID        EventType        StartDateTime          EndDateTime  \
0   325488  Shooting Permit  2017-01-02 00:00:00  2017-01-02 09:00:00   
1   324505  Shooting Permit  2017-01-03 07:00:00  2017-01-03 23:00:00   
2   324505  Shooting Permit  2017-01-03 07:00:00  2017-01-03 23:00:00   
3   324505  Shooting Permit  2017-01-03 07:00:00  2017-01-03 23:00:00   
4   324505  Shooting Permit  2017-01-03 07:00:00  2017-01-03 23:00:00   

             EnteredOn    Category  SubCategoryName  duration_hours  \
0  2016-12-30 05:47:38  Television     Morning Show             9.0   
1  2016-12-16 16:55:04  Television  Episodic series            16.0   
2  2016-12-16 16:55:04  Television  Episodic series            16.0   
3  2016-12-16 16:55:04  Television  Episodic series            16.0   
4  2016-12-16 16:55:04  Television  Episodic series            16.0   

                                            location   latitude  longitude  
0  WEST   44 STREET between BROADWAY and 6 AVENUE...  40.757156 -73.984803  
1  LOCUST AVENUE between EAST  139 STREET and EAS...  40.810089 -73.922740  
2  EAST  140 STREET between LOCUST AVENUE and WAL...  40.808927 -73.918436  
3  WALNUT AVENUE between EAST  139 STREET and EAS...  40.810089 -73.922740  
4  EAST  139 STREET between WALNUT AVENUE and LOC...  40.807513 -73.917024

In [21]:
starting_location = [df['latitude'].mean(),df['longitude'].mean()]
starting_location

[40.765903127927984, -73.74928008374395]

In [30]:
len(df)

29995

In [38]:
map_osm = folium.Map(location=starting_location, zoom_start=10,tiles='cartodbpositron')

mc = MarkerCluster()



#creating a Marker for each point in df_sample. Each point will get a popup with their zip
for row in mapping_df.head(1000).itertuples():
    mc.add_child(folium.Marker(location=[row.latitude,  row.longitude], popup=row.location))
map_osm.add_child(mc)



map_osm

In [67]:
df.columns

Index(['EventID', 'EventType', 'StartDateTime', 'EndDateTime', 'EnteredOn',
       'Category', 'SubCategoryName', 'duration_hours', 'location', 'latitude',
       'longitude'],
      dtype='object')

In [ ]:
df

In [74]:
??FastMarkerCluster

In [92]:
callback = ('function (row) {' 
                'var circle = L.circle(new L.LatLng(row[0], row[1]), {color: "red",  radius: 2000});'
                'return circle};')


callback = """
function (row) {
    var icon, marker;
    icon = L.AwesomeMarkers.icon({
    icon: “map-marker”, markerColor: “red”});
    marker = L.marker(new L.LatLng(row[0], row[1]));
    marker.setIcon(icon);
    return marker;
};
"""

In [100]:
#https://medium.com/@bobhaffner/folium-markerclusters-and-fastmarkerclusters-1e03b01cb7b1
starting_location = [df['latitude'].mean(),df['longitude'].mean()]

map_osm = folium.Map(location=starting_location, zoom_start=10,tiles='cartodbpositron')

for cat in df["Category"].unique():
    feature_group = FeatureGroup(name=cat)
    cat_df = df[df["Category"]==cat]
    #print(len(cat_df))
    feature_group.add_child(FastMarkerCluster(cat_df[['latitude', 'longitude']].values.tolist(), callback=None))
    feature_group.add_to(map_osm)

#feature_group = FeatureGroup(name="student")
#feature_group.add_child(FastMarkerCluster(df[['latitude', 'longitude']].values.tolist(), callback=None))

#feature_group.add_to(map_osm)



LayerControl().add_to(map_osm)
map_osm

In [55]:
film_categories = list(df['Category'].unique())
film_categories

['Television',
 'Theater',
 'Student',
 'Still Photography',
 'Film',
 'Commercial',
 'Documentary',
 'WEB',
 'Music Video']

In [53]:
df['Category'].value_counts()

Television           21130
Film                  4465
Theater               1670
Commercial            1464
Still Photography      646
WEB                    501
Student                 48
Music Video             45
Documentary             26
Name: Category, dtype: int64

In [56]:
?FastMarkerCluster

In [98]:
df[df["Category"]=="Theater"]["SubCategoryName"].value_counts()

Theater    1670
Name: SubCategoryName, dtype: int64

In [95]:
df[df["Category"]=="Television"]["SubCategoryName"].value_counts()

Episodic series            14874
Cable-episodic              4084
Pilot                        606
Not Applicable               479
Made for TV/mini-series      295
News                         237
Special/Awards Show          139
Cable-other                  126
Talk Show                     70
Morning Show                  60
Reality                       56
Variety                       56
Children                      16
Game show                     12
Syndication/First Run         12
Magazine Show                  4
Daytime soap                   3
Cable-daily                    1
Name: SubCategoryName, dtype: int64